In [306]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.image as mpimg

import tempfile
import os
import os.path
import wave
from IPython.display import Audio, display

In [307]:
def list2wav(l):
    b = bytes()
    for sample in l:
        s = int((2**15 - 1) * sample).to_bytes(2, 'little', signed=True)
        b += s
    return b

def play_audio(samples , framerate=8000):
    tf, tfname = tempfile.mkstemp(suffix='.wav', dir='')
    os.close(tf)
    tfname = '' + os.path.basename(tfname)
    w = wave.open(tfname, 'wb')
    w.setnchannels(1)
    w.setsampwidth(2)
    w.setframerate(framerate)
    w.setnframes(len(samples))
    if not isinstance(samples, list):
        samples = samples.tolist()
    w.writeframes(list2wav(samples))
    w.close()

    return Audio(tfname)

def chunks(l, n):
    for i in range(0, len(l), n):
        yield l[i:i + n]

def open_audio(filename):
    f = wave.open(filename, 'rb')
    b = f.readframes(f.getnframes())
    t = np.linspace(0, f.getnframes()/f.getframerate(), f.getnframes())
    f.close()    
    r = []
    for c in chunks(b, 2):
        r.append(int.from_bytes(c, byteorder='little', signed=True) / (2**15 - 1))
    return t, np.array(r)

In [322]:
x1, y1 = open_audio('./FOBIseparateX.wav')
play_audio(y1,framerate=21000)

In [321]:
x2, y2 = open_audio('./FOBIseparateY.wav')
play_audio(y2,framerate=21000)

In [337]:
from sklearn import preprocessing
S=np.vstack((y1,y2)).T

#S = preprocessing.scale(S)
# Mix data
A = np.array([[0.5, -0.5], [0.5, 0.5]])  # Mixing matrix
X = np.dot(S, A.T)  # Generate observations
print(A)
X[:, 0]

[[ 0.5 -0.5]
 [ 0.5  0.5]]


array([0., 0., 0., ..., 0., 0., 0.])

In [341]:
x,y = open_audio('./ja1.wav')
play_audio(y,framerate=84000)

In [342]:
play_audio(X[:, 0],framerate=21000)

In [340]:
play_audio(X[:, 1],framerate=21000)

In [343]:
from sklearn.decomposition import FastICA
# Compute ICA
ica = FastICA(n_components=2)
S_ = ica.fit_transform(X)  # Reconstruct signals
A_ = ica.mixing_  # Get estimated mixing matrix

#S_ = preprocessing.scale(S_)
# plt.plot(S_[:,0])
# plt.show()

In [345]:
play_audio(10*S_[:, 0],framerate=21000)


In [346]:
play_audio(10*S_[:, 1],framerate=21000)